<img src="resources/tag_metters_Logo.png" width="299" height="45">

## #Tag is invisible but it does actually track the trends
To understand how tags play the role by using it on NYTimes daily and how people really react about the topic by looking at other media platforms through NYTimes tags.

In [12]:
import sys
sys.executable

'/usr/local/opt/python/bin/python3.7'

In [13]:
sys.path

['/Users/hh/Documents/Pratt/Adv.ProjectsinVis/Monthly-Frequency-of-NYTimes-Tag',
 '/usr/local/Cellar/python/3.7.7/Frameworks/Python.framework/Versions/3.7/lib/python37.zip',
 '/usr/local/Cellar/python/3.7.7/Frameworks/Python.framework/Versions/3.7/lib/python3.7',
 '/usr/local/Cellar/python/3.7.7/Frameworks/Python.framework/Versions/3.7/lib/python3.7/lib-dynload',
 '',
 '/Users/hh/Library/Python/3.7/lib/python/site-packages',
 '/usr/local/lib/python3.7/site-packages',
 '/usr/local/lib/python3.7/site-packages/IPython/extensions',
 '/Users/hh/.ipython']

In [14]:
import json
import requests
import pandas as pd
import numpy as np
import operator
import time
import praw
import nltk
import configparser

from apiclient import discovery
from datetime import datetime
from dateutil.relativedelta import relativedelta

from pytrends.request import TrendReq
from praw.models import MoreComments
from googleapiclient import discovery
from textblob import TextBlob
from pandas.io.json import json_normalize

import pprint
import matplotlib.pyplot as plt
import seaborn as sns

In [15]:
from sqlalchemy import create_engine
from sqlalchemy.ext.declarative import declarative_base
from sqlalchemy import Table, Column, Integer, String, MetaData, ForeignKey

from sqlalchemy.orm import sessionmaker

In [16]:
from sqlalchemy import *
from sqlalchemy.ext.declarative import declarative_base
from sqlalchemy.sql import *
from sqlalchemy.orm import relationship

In [17]:
# Use CofigParser to safely store the password or key
config = configparser.ConfigParser()
config.read('key_pair.ini')

Times_key = config['Times']['key']

Reddit_client_id = config['Reddit']['client_id']
Reddit_client_secret = config['Reddit']['client_secret']
Reddit_username = config['Reddit']['username']
Reddit_password = config['Reddit']['password']
Reddit_user_agent = config['Reddit']['user_agent']

Youtube_service_name = config['Youtube']['YOUTUBE_API_SERVICE_NAME']
Youtube_API_version = config['Youtube']['YOUTUBE_API_VERSION']
Youtube_developer_key = config['Youtube']['DEVELOPER_KEY']

### Storing Data using SQLalchemy

In [18]:
engine = create_engine('sqlite:///monthly_times_tags.db', echo=True)
Base = declarative_base()

In [19]:
class TimesTable(Base): 
    __tablename__ = 'times'
    __table_args__ = {'extend_existing': True}

    id = Column(Integer, primary_key=True)
    tag = Column(String(255))
    periodeM = Column(String(25))
    frequency = Column(Integer)
    title = Column(String(255))
    date = Column(String(25))
    url = Column(String(255))
    img_URL = Column(String(255))

class GoogleTable(Base): 
    __tablename__ = 'google'
    __table_args__ = {'extend_existing': True}

    id = Column(Integer, primary_key=True)
    trendDate = Column(PickleType)
    busiest = Column(String(25))
    trendIndex = Column(PickleType)
    fk_times = Column(Integer, ForeignKey("times.id", ondelete='CASCADE'), nullable=False)
    googleNTag = relationship('TimesTable')


class RedditTable(Base): 
    __tablename__ = 'reddit'
    __table_args__ = {'extend_existing': True}

    id = Column(Integer, primary_key=True)
    tag = Column(String(255))
    commentCount = Column(Integer)
    
class YoutubeTable(Base): 
    __tablename__ = 'youtube'
    __table_args__ = {'extend_existing': True}

    id = Column(Integer, primary_key=True)
    tag = Column(String(255))
    viewCount = Column(Integer)
    commentCount = Column(Integer)
    likeCount = Column(Integer)

# TimesTable.__table__.create(bind=engine, checkfirst=True)
# GoogleTable.__table__.create(bind=engine, checkfirst=True)
# RedditTable.__table__.create(bind=engine, checkfirst=True)
# YoutubeTable.__table__.create(bind=engine, checkfirst=True)

### New York Times API
https://developer.nytimes.com/apis

Archive API
- Finds all articles's metadata from archive APi (about 7000 every month): title, section_name, period, url, word_count, keywords

In [574]:
def cleaning_tag(tag):
    if tag in ['Trump', 'Donald J']:
        tag = 'Donald Trump'
    if tag in ['Joseph R Jr', 'Biden']:
        tag = 'Joe Biden'
    if tag in ['Brett M', 'Supreme Court (US)', 'Kavanaugh']:
        tag = 'Brett Kavanaugh'
    if tag in ['Putin', 'Vladimir V']:
        tag = 'Putin'
    if tag in ['Barr', 'William P']:
        tag = 'Barr William P'
    if tag in ['Mueller', 'Robert S III']:
        tag = 'Mueller Robert S III'
    if tag in ['Sanders, Bernard', 'Sanders', 'Bernard', 'Bernie Sanders']:
        tag = 'Bernie Sanders'
    if tag in ['Pete Buttigieg', 'Buttigieg, Pete (1982- )', 'Buttigieg', 'Pete Buttigieg', 'Pete (1982- )']:
        tag = 'Pete Buttigieg'
    if tag in ['Michael R', 'Bloomberg']:
        tag = 'Michael Bloomberg'
    if tag in ['Suleimani', 'Qassim']:
        tag = 'Soleimani Qassem'
    if tag in ['Warren', 'Elizabeth']:
        tag = 'Elizabeth Warren'
    if tag in ['Coronavirus Aid', 'Relief', 'and Economic Security Act (2020)']:
        tag = 'Coronavirus Aid, Relief, and Economic Security Act (2020)'
    if tag in ['School Shootings and Armed Attacks']:
        tag = 'School Shootings'
    if tag in ['Midland-Odessa, Tex, Shooting (2019)', 'Dayton, Ohio, Shooting (2019)', 'El Paso, Tex, Shooting (2019)', 'El Paso', 'Dayton', 'Shooting (2019)', 'Tex']:
        tag = 'Shootings'
    if 'Russian Interference in 2016' in tag:
        tag = 'Russian interference in the 2016 United States elections'
    if tag in ['Homosexuality and Bisexuality']:
        tag = 'Homosexuality'
    if 'Trump-Ukraine' in tag:
        tag = 'Trump Ukraine Whistle blower'
    if tag in ['Biden, Joseph R Jr', 'Biden']:
        tag = 'Joe Biden'
    if tag in ['Sanders, Bernard', 'Sanders', 'Bernard', 'Bernie Sanders']:
        tag = 'Bernie Sanders'
    if tag in ['Pete Buttigieg', 'Buttigieg, Pete (1982- )', 'Buttigieg', 'Pete Buttigieg', 'Pete (1982- )']:
        tag = 'Pete Buttigieg'
    if tag in ['Blacks', 'Black People']:
        tag = 'Blacks'
    if 'Shutdowns' in tag:
        tag = 'Shutdowns'
    if 'Quarantine' in tag:
        tag = 'Quarantines'
    if 'Deaths' in tag:
        tag = 'Deaths'
    if 'Child' in tag:
        tag = 'Parenting'
    if 'Syria' in tag:
        tag = 'Syria'
    if tag in ['Donald Trump', 'Weddings and Engagements', 'Impeachment', 'Senate', 'Discrimination', 'Art', 'Debates (Political)', 'Demonstrations' , 'Protests and Riots', 'Women and Girls','States (US)', 'United States', 'New York State', 'New York City', 'NYC', 'NY)', 'Primaries and Caucuses', 'United States Politics and Government', 'Politics and Government', 'Books and Literature', 'Television', 'Movies', 'Real Estate and Housing (Residential)', 'United States', 'United States International Relations', 'Primaries and Caucuses', 'United States Economy', 'Elections']:
        tag = ''
    return tag

In [575]:
def get_NYTimes_metadata():

    # To get most frequently used tag in NYTimes
    today = str(datetime.today())
    monthly_archive = {}
    frequent_tags_archive = {}

    for yy in reversed(range(2019, int(today[:4]) + 1)):
        if str(yy) == today[:4]:
            ends = int(today[5:7]) + 1
            start = 1
        else:
            ends = 13
            if '0' in today[5:7]:
                start = int(today[6:7])
            else:
                start = int(today[5:7])

        for mm in reversed(range(start,ends)):
            if len(str(mm)) == 1:
                date_not_duplicate = str(yy) + '-0' + str(mm)
            else:
                date_not_duplicate = str(yy) + '-' + str(mm)
#             print('--match--',date_not_duplicate)
#             print('in it?', monthly_archive.keys())
            if date_not_duplicate not in monthly_archive:
                parameters = {'api-key': Times_key}           
                archived_Url = 'https://api.nytimes.com/svc/archive/v1/'+ str(yy) +'/'+ str(mm) +'.json'
                archives = requests.get(archived_Url, params=parameters).json()

                monthly_article = []
                for a in archives['response']['docs']:
#                     print('* * * ', a['headline']['main'])
                    articles = {}
                    articles['title'] = a['headline']['main']
                    articles['pub_date'] = a['pub_date'][:10]
                    articles['url'] = a['web_url']
                    
                    if len(a['multimedia']) !=0 and a['multimedia'][0]['url']:
                        articles['thm_img'] = 'https://static01.nyt.com/' + a['multimedia'][0]['url']
                    else:
                        articles['thm_img'] = 'no_image_found'
                        
                    articles['tags'] = [''.join(tag['value']) for tag in a['keywords']]
                    cleaning_List = map(cleaning_tag,  articles['tags'])
                    articles['tags'] = [changed_tag for changed_tag in cleaning_List]
                    
                    monthly_article.append(articles)
                    
                if len(str(mm)) == 1:
                    mm = '0' + str(mm)
                monthly_archive[str(yy)+'-'+str(mm)] = monthly_article

                tag_arr = []
                for m in monthly_article:
                    for t in m['tags']:
                        for string in t.split(', '):
                            tag_arr.append(', '.join(string.split(', ')))
                cleaning_List=map(cleaning_tag,  tag_arr)
                tag_arr = [changed_tag for changed_tag in cleaning_List]
#                 print('* * * ', tag_arr)
                count_tag = {}
                for tag in tag_arr:
                    if tag is not '':
                        if tag in count_tag:
                            count_tag[tag] += 1
                        else:
                            count_tag[tag] = 1   

                # This variable is what we want to get in NYTimes
                tags_with_frequency = sorted(count_tag.items(),key=operator.itemgetter(1),reverse=True)[:10]
                frequent_tags_archive[str(yy)+'-'+str(mm)] = tags_with_frequency

    return monthly_archive, frequent_tags_archive

In [576]:
monthly_archive = get_NYTimes_metadata()[0]
frequent_tags_archive = get_NYTimes_metadata()[1]
frequent_tags_archive

{'2020-05': [('Coronavirus (2019-nCoV)', 2495),
  ('Quarantines', 956),
  ('Deaths', 394),
  ('Coronavirus Aid, Relief, and Economic Security Act (2020)', 390),
  ('Parenting', 333),
  ('Shutdowns', 274),
  ('Presidential Election of 2020', 241),
  ('Coronavirus Reopenings', 196),
  ('Epidemics', 188),
  ('Labor and Jobs', 163)],
 '2020-04': [('Coronavirus (2019-nCoV)', 3978),
  ('Parenting', 1278),
  ('Quarantines', 983),
  ('Coronavirus Aid, Relief, and Economic Security Act (2020)', 807),
  ('Deaths', 568),
  ('Presidential Election of 2020', 537),
  ('Epidemics', 435),
  ('Shutdowns', 264),
  ('Hospitals', 249),
  ('Babies and Infants', 206)],
 '2020-03': [('Coronavirus (2019-nCoV)', 3463),
  ('Quarantines', 860),
  ('Presidential Election of 2020', 813),
  ('Epidemics', 650),
  ('Democratic Party', 424),
  ('Joe Biden', 415),
  ('Shutdowns', 372),
  ('Bernie Sanders', 353),
  ('Deaths', 333),
  ('Parenting', 310)],
 '2020-02': [('Presidential Election of 2020', 855),
  ('Coronavir

In [577]:
monthly_archive

{'2020-05': [{'title': 'Seven States to Coordinate on Amassing Medical Equipment to Fight Coronavirus',
   'pub_date': '2020-05-03',
   'url': 'https://www.nytimes.com/2020/05/03/nyregion/coronavirus-new-york-update.html',
   'thm_img': 'https://static01.nyt.com/images/2020/05/03/nyregion/03nyvirus-briefing-top01/merlin_172147824_5d1a7132-5b95-40ac-b1c5-f1914d8534b3-articleLarge.jpg',
   'tags': ['Coronavirus (2019-nCoV)', '', '']},
  {'title': 'The Courage to Be Alone',
   'pub_date': '2020-05-01',
   'url': 'https://www.nytimes.com/2020/05/01/opinion/sunday/coronavirus-parenting-isolation.html',
   'thm_img': 'https://static01.nyt.com/images/2020/05/03/opinion/sunday/03craig/03craig-articleLarge.jpg',
   'tags': ['Philosophy',
    'Parenting',
    'Parenting',
    'Quarantines',
    'Coronavirus (2019-nCoV)']},
  {'title': 'Tennis Coming Back Slowly With Exhibition Matches',
   'pub_date': '2020-05-01',
   'url': 'https://www.nytimes.com/2020/05/01/sports/tennis/coronavirus-tennis.ht

In [324]:
def store_times(monthly_archive, frequent_tags_archive):
    # Pytrend and PRAW use "frequent_tags_archive" in order to get each demand data
    multi_articles = {}
    for periode in frequent_tags_archive:
        print('Check', frequent_tags_archive[periode])     
        for top_tag in frequent_tags_archive[periode]:
            # Get specific NYTimes article information per each tags
            for whole_month in list(monthly_archive.values()):
                for each in reversed(whole_month):
                    if top_tag[0] in multi_articles and periode in multi_articles[top_tag[0]]:
                        pass                             
                    else:
                        # print(top_tag[0] in each['tags'])
                        if len(each['tags']) != 0 and top_tag[0] in each['tags']:
                            # print('If True, ', top_tag[0])
                            try:
                                print(top_tag[0])
                                multi_articles[top_tag[0]] = periode
                            except Exception as e:
                                print(" = Unable insert_TimesTag to DB : ", e, " =")
                                pass   
            
    return #multi_articles

### Find the most appeared tags among these days

In [270]:
dicts= {}
for periode in frequent_tags_archive:
    count = 0
    for tags in frequent_tags_archive[periode]:
        if tags[0] not in dicts:
#             count = count + 1
            dicts[tags[0]] = tags[1]
        else:
            dicts[tags[0]] = dicts[tags[0]] + tags[1]
tags_with_frequency = sorted(dicts.items(),key=operator.itemgetter(1),reverse=True)[:10]
                
pprint.pprint(tags_with_frequency)

[('Coronavirus (2019-nCoV)', 9730),
 ('Presidential Election of 2020', 6085),
 ('Joe Biden', 4701),
 ('Parenting', 3905),
 ('Deaths', 3514),
 ('Quarantines', 2565),
 ('Bernie Sanders', 2564),
 ('United States International Relations', 2327),
 ('Trump-Ukraine', 2111),
 ('China', 1968)]


### Find the General Tags overtime

In [29]:
tag_arr = []
for period in monthly_archive:
    for article in monthly_archive[period]:
        for t in article['tags']:
            for string in t.split(', '):
                tag_arr.append(', '.join(string.split(', ')))

count_tag = {}
for tag in tag_arr:
    if tag in count_tag:
        count_tag[tag] += 1
    else:
        count_tag[tag] = 1   

# This variable is what we want to get in NYTimes
general_tags = sorted(count_tag.items(),key=operator.itemgetter(1),reverse=True)[:20]

pprint.pprint(general_tags)

[('Trump', 10561),
 ('Donald J', 10334),
 ('United States Politics and Government', 10304),
 ('Coronavirus (2019-nCoV)', 9378),
 ('Presidential Election of 2020', 6039),
 ('Politics and Government', 4710),
 ('Democratic Party', 4037),
 ('NY)', 3972),
 ('Books and Literature', 3685),
 ('Movies', 3241),
 ('New York City', 3092),
 ('Television', 2767),
 ('United States International Relations', 2704),
 ('United States', 2500),
 ('China', 2440),
 ('Biden', 2426),
 ('Real Estate and Housing (Residential)', 2376),
 ('Trump-Ukraine Whistle-blower Complaint and Impeachment Inquiry', 2280),
 ('Joseph R Jr', 2206),
 ('Deaths (Obituaries)', 2153)]


### Pytrends API
https://pypi.org/project/pytrends/

Sample codes to see Google doesn't block my IP

In [219]:
pytrends = TrendReq(hl='en-US', tz=360, timeout=(10,25))
tag_arr = ['Coronavirus (2019-nCoV)']
pytrends.build_payload(tag_arr, cat=0, timeframe='2020-04-01 ' + str(datetime.now())[:10], geo='', gprop='')
time.sleep(2)
df = pytrends.interest_over_time().reset_index()
df.head()

date  Coronavirus (2019-nCoV)  isPartial
0 2020-04-01                       75      False
1 2020-04-02                       44      False
2 2020-04-03                       56      False
3 2020-04-04                       74      False
4 2020-04-05                       87      False

In [118]:
# Get a unique tag collection for the search query
def get_trends_Tags(frequent_tags_archive): 
    today = str(datetime.today())
    combined_monthly_tag = {}
    
    for time_period in frequent_tags_archive:
        tag_only = []
        for each in frequent_tags_archive[time_period]:    
            tag_only.append(each[0])
            combined_monthly_tag[time_period] = tag_only
        
    pytrends = TrendReq(hl='en-US', tz=360)
    monthly_interests = {}
    
    for period in combined_monthly_tag:
        data = []
        for tag in combined_monthly_tag[period]:
            tag_arr = []
            tag_arr.append(tag)
            print(tag)
            interest_over_time = {}
            
            try:
                pytrends.build_payload(tag_arr, cat=0, timeframe = '2019-05-01 '+ today[:10], geo='', gprop='')
                df = pytrends.interest_over_time().reset_index()
            except Exception as e:
                print(tag_arr, ', and which reason? ', e)
                pass
            
            interest_over_time['Tag'] = tag
            try:
                interest_over_time['StartDate'] = one_month_ago
                interest_over_time['EndDate'] = one_month_later
                interest_over_time['Rate'] = [rate for rate in df[tag]]
            except Exception as e:
                pass
            data.append(interest_over_time)     
        monthly_interests[period] = data
    return monthly_interests

In [119]:
monthly_interests = get_trends_Tags(frequent_tags_archive)

Coronavirus (2019-nCoV)
Quarantines
Deaths
Coronavirus Aid, Relief, and Economic Security Act (2020)


KeyboardInterrupt: 

### Reddit API
https://praw.readthedocs.io/en/latest/

In [391]:
frequent_tags_archive = {'2020-05': [('Coronavirus (2019-nCoV)', 1176),
  ('Quarantines', 445)],
 '2020-04': [('Coronavirus (2019-nCoV)', 3978),
  ('Parenting', 1278)],
 '2020-03': [('Coronavirus (2019-nCoV)', 3463),
  ('Quarantines', 860)],
 '2020-02': [('Presidential Election of 2020', 855),
  ('Bernie Sanders', 704)],
 '2020-01': [('Presidential Election of 2020', 668),
  ('Trump-Ukraine', 472)],
 '2019-12': [('Presidential Election of 2020', 346),
  ('Trump-Ukraine', 324)],
 '2019-11': [('Trump-Ukraine', 532),
  ('Presidential Election of 2020', 417)]}

In [392]:
def call_combined_monthly_tag(frequent_tags_archive):
    combined_monthly_tag = {}
    for time_period in frequent_tags_archive.keys():
        tag_only = []
        for each in frequent_tags_archive[time_period]:    
#             print(each[0])
            tag_only.append(each[0])
            combined_monthly_tag[time_period] = tag_only
    return combined_monthly_tag

In [567]:
def Overall_Unique_tag_with_frequency(frequent_tags_archive):
    overall_Unique_tag_with_frequency={}
    for periode in frequent_tags_archive:
        for tag_with_F in frequent_tags_archive[periode]:
            if tag_with_F[0] in overall_Unique_tag_with_frequency:
                overall_Unique_tag_with_frequency[tag_with_F[0]] = tag_with_F[1] + overall_Unique_tag_with_frequency[tag_with_F[0]]
            else:
                overall_Unique_tag_with_frequency[tag_with_F[0]] = tag_with_F[1]

    overall_Unique_tag_with_frequency = sorted(overall_Unique_tag_with_frequency.items(),key=operator.itemgetter(1),reverse=True)
    return overall_Unique_tag_with_frequency

In [568]:
call_combined_monthly_tag(frequent_tags_archive)

{'2020-05': ['Coronavirus (2019-nCoV)',
  'Quarantines',
  'Coronavirus Aid, Relief, and Economic Security Act (2020)',
  'Deaths',
  'Parenting',
  'Shutdowns',
  'Presidential Election of 2020',
  'Coronavirus Reopenings',
  'Epidemics',
  'Joe Biden'],
 '2020-04': ['Coronavirus (2019-nCoV)',
  'Parenting',
  'Quarantines',
  'Coronavirus Aid, Relief, and Economic Security Act (2020)',
  'Deaths',
  'Presidential Election of 2020',
  'Epidemics',
  'Shutdowns',
  'Hospitals',
  'Babies and Infants'],
 '2020-03': ['Coronavirus (2019-nCoV)',
  'Quarantines',
  'Presidential Election of 2020',
  'Epidemics',
  'Democratic Party',
  'Joe Biden',
  'Shutdowns',
  'Bernie Sanders',
  'Deaths',
  'Parenting'],
 '2020-02': ['Presidential Election of 2020',
  'Coronavirus (2019-nCoV)',
  'Democratic Party',
  'Bernie Sanders',
  'China',
  'Epidemics',
  'Joe Biden',
  'Deaths',
  'Michael Bloomberg',
  'Bloomberg'],
 '2020-01': ['Presidential Election of 2020',
  'Soleimani Qassem',
  'Trump

In [569]:
unique_tag_only_with_frequency = Overall_Unique_tag_with_frequency(frequent_tags_archive)
unique_tag_only_with_frequency

[('Coronavirus (2019-nCoV)', 10493),
 ('Presidential Election of 2020', 6178),
 ('Parenting', 3892),
 ('Democratic Party', 3817),
 ('Deaths', 3617),
 ('Quarantines', 2843),
 ('Trump Ukraine Whistle blower', 2116),
 ('China', 1554),
 ('Joe Biden', 1530),
 ('Epidemics', 1522),
 ('Coronavirus Aid, Relief, and Economic Security Act (2020)', 1233),
 ('Shutdowns', 923),
 ('Bernie Sanders', 910),
 ('Computers and the Internet', 632),
 ('House of Representatives', 554),
 ('Republican Party', 544),
 ('Ukraine', 544),
 ('Immigration and Emigration', 530),
 ('Soleimani Qassem', 514),
 ('United States Defense and Military Forces', 469),
 ('Blacks', 469),
 ('Mueller Robert S III', 454),
 ('International Trade and World Market', 409),
 ('Iran', 345),
 ('Michael Bloomberg', 259),
 ('Shooting (2019)', 254),
 ('Hospitals', 249),
 ('Bloomberg', 242),
 ('Syria', 233),
 ('Barr William P', 220),
 ('Babies and Infants', 206),
 ('Islamic State in Iraq and Syria (ISIS)', 188),
 ('Coronavirus Reopenings', 187)

### Youtube API
https://developers.google.com/youtube/v3/docs/search/list?hl=en_US

In [522]:
def call_Youtube(unique_tag_only_with_frequency):
    # creating Youtube Resource Object 
    youtube_object = discovery.build(Youtube_service_name, Youtube_API_version, developerKey = Youtube_developer_key)

    max_results = 2
    youtube_metadata = []
    
    for tag_frequency in unique_tag_only_with_frequency[:2]:
        viewCount = 0
        commentCount = 0
        likeCount = 0
        turned_off_comments = 0
        
        video = {}
        contain_stats = {}
        
        time.sleep(2)
        search_tags = youtube_object.search().list(q = tag_frequency[0], part = "id, snippet", order = 'relevance', maxResults = max_results, publishedAfter = "2020-01-01T00:00:00Z").execute() 
        time.sleep(2)
        
        for item in search_tags.get("items", []):
            try:
                time.sleep(2)
                stats = youtube_object.videos().list(part='statistics, snippet', id=item["id"]["videoId"]).execute()
                time.sleep(2)
                viewCount = int(stats.get("items", [])[0]['statistics']['viewCount'])
#                 print('viewCount, ', viewCount)
                likeCount =  int(stats.get("items", [])[0]['statistics']['likeCount'])
#                 print('likeCount, ', likeCount) 
                commentCount = int(stats.get("items", [])[0]['statistics']['commentCount'])
#                 print('commentCount, ', commentCount)

            except Exception as e:
                print(" = Unable search Youtube : ", tag_frequency[0], " =", e)
                if e == 'commentCount':
                    new_likeCount = 0 #'Comments are turned off'
                    contain_stats['turned_off_comments'] = 0
                elif e == 'likeCount':
                    new_likeCount = 0
                elif e == 'viewCount':
                    new_viewCount = 0

            if 'viewCount' in contain_stats:
                contain_stats['viewCount'] = contain_stats['viewCount'] + viewCount
            else:
                contain_stats['viewCount'] = viewCount
            if 'commentCount' in contain_stats:
                contain_stats['commentCount'] = contain_stats['commentCount'] + commentCount
            else:
                contain_stats['commentCount'] = commentCount
            if 'likeCount' in contain_stats:
                contain_stats['likeCount'] = contain_stats['likeCount'] + likeCount
            else:
                contain_stats['likeCount'] = likeCount
            if 'turned_off_comments' in contain_stats:
                contain_stats['turned_off_comments'] = contain_stats['turned_off_comments'] + 1
            
            if tag_frequency[0] in video.keys():
                pass
            else:
                video[tag_frequency[0]] = contain_stats
                
        youtube_metadata.append(video)
        
    return youtube_metadata

In [523]:
call_Youtube(unique_tag_only_with_frequency)

contain_stats:  {'viewCount': 5272627, 'commentCount': 1984, 'likeCount': 28831}
contain_stats:  {'viewCount': 7633257, 'commentCount': 6551, 'likeCount': 54631}
 = Unable search Youtube :  Presidential Election of 2020  = 'commentCount'
contain_stats:  {'viewCount': 68079, 'commentCount': 0, 'likeCount': 345}
contain_stats:  {'viewCount': 93881, 'commentCount': 113, 'likeCount': 507}


[{'Coronavirus (2019-nCoV)': {'viewCount': 7633257,
   'commentCount': 6551,
   'likeCount': 54631}},
 {'Presidential Election of 2020': {'viewCount': 93881,
   'commentCount': 113,
   'likeCount': 507}}]

In [536]:
 = Unable search Youtube :  Coronavirus (2019-nCoV)  = 'likeCount'
 = Unable search Youtube :  Presidential Election of 2020  = 'commentCount'
 = Unable search Youtube :  Presidential Election of 2020  = 'commentCount'
 = Unable search Youtube :  Parenting  = 'likeCount'
 = Unable search Youtube :  United States International Relations  = 'commentCount'
 = Unable search Youtube :  United States International Relations  = 'commentCount'
 = Unable search Youtube :  United States International Relations  = 'commentCount'
 = Unable search Youtube :  United States International Relations  = 'commentCount'
 = Unable search Youtube :  United States International Relations  = 'commentCount'
 = Unable search Youtube :  United States International Relations  = 'commentCount'
 = Unable search Youtube :  Trump Ukraine Whistle blower  = 'commentCount'
 = Unable search Youtube :  Trump Ukraine Whistle blower  = 'likeCount'
 = Unable search Youtube :  Joe Biden  = 'commentCount'
 = Unable search Youtube :  Joe Biden  = 'likeCount'
 = Unable search Youtube :  Computers and the Internet  = 'likeCount'
 = Unable search Youtube :  Coronavirus Aid, Relief, and Economic Security Act (2020)  = 'commentCount'
 = Unable search Youtube :  Coronavirus Aid, Relief, and Economic Security Act (2020)  = 'likeCount'
 = Unable search Youtube :  California  = 'commentCount'
 = Unable search Youtube :  Shutdowns  = 'commentCount'
 = Unable search Youtube :  Shutdowns  = 'commentCount'

7633257

## Not using anymore

- Top Stories API: (about 30 articles by 7 days): title, pub_date, url, section, des_facet, geo_facet
- Newswire API: Finds by Archive API's url : des_facet
- Most Popular API
- Top Stories API, Times Tags API, Community API

## Reddit

In [ ]:
nltk.download('averaged_perceptron_tagger')

In [246]:
def get_reddit_comments(overall_Unique_tag_with_frequency):
    
    reddit = praw.Reddit(client_id = Reddit_client_id,
                         client_secret = Reddit_client_secret,
                         username = Reddit_username,
                         password = Reddit_password,
                         user_agent = Reddit_user_agent)
#     times_metadata = {'2020-04':['Coronavirus (2019-nCoV)', 'Quarantines', 'Parenting'], '2019-04': ['China', 'Epidemics', 'Deaths (Fatalities)']}

    reddit_metadata = []
    for tag_frequency in overall_Unique_tag_with_frequency:
        subreddit = reddit.subreddit('all')
        time.sleep(2)

        each_tag = {}
        for i, post in enumerate(subreddit.search(tag_frequency[0], sort='relevance', syntax='lucene', limit=3)):
            count = 0;
            if not post.stickied:
                each_tag['Tag'] = tag_frequency[0]
#                 print('* *',tag_frequency[0])
#                 each_tag['Title'] = post.title
#                 each_tag['CreatedAt'] = datetime.fromtimestamp(post.created_utc).isoformat()[:10]
#                 each_tag['DiscussionAbout'] = post.url
#                 print('* * *', post.url)
                each_tag_comments = post.comments.list()
                comments_arr = []
                for comment in each_tag_comments:
                    if isinstance(comment, MoreComments):
                        continue
                    comments_arr.append(comment.body)
                    count = count + len(comments_arr)
                each_tag['comments'] = count

        reddit_metadata.append(each_tag)
                    
    return reddit_metadata

In [173]:
def get_reddit_Posts(times_metadata):   
#     result = {}
#     for time_period in times_metadata:
#         data = []
#         for each in times_metadata[time_period]:     
#             data.append(each['Tag'])
#             result[time_period] = data  
            
    reddit = praw.Reddit(client_id = Reddit_client_id,
                         client_secret = Reddit_client_secret,
                         username = Reddit_username,
                         password = Reddit_password,
                         user_agent = Reddit_user_agent)
    result = {'2020-04':['Coronavirus (2019-nCoV)', 'Quarantines', 'Parenting'], '2019-04': ['China', 'Epidemics', 'Deaths (Fatalities)']}
 
    reddit_metadata = []
    for period in result:
        print(period + ': ', len(result[period]))
        reddit_posts = {}
        add_post_arr = []
        for tag in result[period]:
            subreddit = reddit.subreddit('all')
            time.sleep(2)
            for i, post in enumerate(subreddit.search(tag, sort='relevance', syntax='lucene', limit=100)):
                if not post.stickied:
                    each_tag = {}
                    each_tag['Tag'] = tag
#                     print('--1--',tag)
                    each_tag['Title'] = post.title
                    each_tag['CreatedAt'] = datetime.fromtimestamp(post.created_utc).isoformat()[:10]
                    each_tag['DiscussionAbout'] = post.url
                    each_tag['Ups'] = post.ups
                    each_tag['Downs'] = post.downs
                    add_post_arr.append(each_tag)
        reddit_posts[period] = add_post_arr
        reddit_metadata.append(reddit_posts)
#         print('--2--',reddit_metadata)
    
#     add_tag = {}
#     for item in reddit_metadata:
#         for period in item: 
#             monthly_posts = []
#             byTime = {}
            
#             for each_post in item[period]:
#                 each_post['CreatedAt'] = each_post['CreatedAt'][:7]

#                 if each_post['Tag'] in add_tag:
#                     if each_post['CreatedAt'] in byTime:
#                         byTime[each_post['CreatedAt']][0] += 1
#                         byTime[each_post['CreatedAt']][1] += each_post['Ups']
#                     else:
#                         add_freq_votes = []
#                         byTime[each_post['CreatedAt']] = add_freq_votes
#                         add_freq_votes.append(1)
#                         add_freq_votes.append(each_post['Ups'])
#                 else:
#                     add_tag[each_post['Tag']] = byTime
#                     if each_post['CreatedAt'] in byTime:
#                         byTime[each_post['CreatedAt']][0] += 1
#                         byTime[each_post['CreatedAt']][1] += each_post['Ups']
#                     else:
#                         add_freq_votes = []
#                         byTime[each_post['CreatedAt']] = add_freq_votes
#                         add_freq_votes.append(1)
#                         add_freq_votes.append(each_post['Ups'])
# #                     print('--1--', add_tag)
#             monthly_posts.append(add_tag)
# #             print('--2--', monthly_posts)
    
# #     print('--3--', monthly_posts)
    return reddit_metadata

In [138]:
frequent_tags_archive = {'2020-04': [('Coronavirus (2019-nCoV)', 3591),
  ('Quarantines', 822)]}

In [ ]:
 # reddit = praw.Reddit(client_id = Reddit_client_id,
    #                      client_secret = Reddit_client_secret,
    #                      username = Reddit_username,
    #                      password = Reddit_password,
    #                      user_agent = Reddit_user_agent)
    # reddit_metadata = []
    
    # # Store numbers of each Reddit's comments into DB
    # try:
    #     print('Check tag existing on Reddit: ', tag_frequency[0])
    #     subreddit = reddit.subreddit('all')
    #     time.sleep(2)

    #     each_tag = {}
    #     for post in subreddit.search(tag_frequency[0], sort='relevance', syntax='lucene', time_filter='month', limit=max_results):
    #         count = 0;
    #         if not post.stickied:
    #             each_tag['Tag'] = tag_frequency[0]
    #             each_tag_comments = post.comments.list()
    #             comments_arr = []
    #             for comment in each_tag_comments:
    #                 if isinstance(comment, MoreComments):
    #                     continue
    #                 comments_arr.append(comment.body)
    #                 count = count + len(comments_arr)
    #             each_tag['commentCount'] = count
    # except Exception as e:
    #     print(" = Unable search Reddit : ", tag_frequency[0], " =")
    #     pass
    
    # reddit_metadata.append(each_tag)

    # print('= reddit_metadata =', reddit_metadata)

    # for each_reddit in reddit_metadata:    
    #     try:
    #         insert_Reddit = RedditTable(
    #             tag=each_reddit['tag'],
    #             commentCount=each_reddit['commentCount']
    #         )
    #         session.add(insert_Reddit)

    #     except Exception as e:
    #         print(" = Unable insert_Reddit to DB : ", tag_frequency[0], " =")
    #         pass

In [ ]:
def get_sentimental_chart(reddit_metadata):
    tags_metadata = []
    for single_tag in reddit_metadata:
        tag_sentiment = {}
        avg_polarity = 0
        pos_count = 0
        neg_count = 0
        neutral_count = 0
        for single_comment in single_tag['Comments']: 
            
            # Get Word Sentimental analysis
            blobed_word = TextBlob(single_comment)
            if blobed_word.sentiment.polarity > 0:
                pos_count += 1
            elif blobed_word.sentiment.polarity == 0:
                neutral_count += 1
            else:
                neg_count += 1      
            avg_polarity += blobed_word.sentiment.polarity
            
            tag_sentiment['tag'] = single_tag['Tag']    
            tag_sentiment['avg_polarity'] = avg_polarity / len(single_tag['Comments'])
            tag_sentiment['pos_count'] = pos_count
            tag_sentiment['neg_count'] = neg_count
            tag_sentiment['neutral_count'] = neutral_count
            
            # Get Adjective words' frequencies
            adgs_arr = []
            for blobed_tags in blobed_word.tags:
                if blobed_tags[1] in ['JJ', 'JJR', 'JJS']:
                    adgs_arr.append(blobed_tags[0])
            adg_frequency = {}
            for adg in adgs_arr: 
                if adg in adg_frequency:
                    adg_frequency[adg] += 1
                else:
                    adg_frequency[adg] = 1 
            tag_sentiment['adg_frequency'] = sorted(adg_frequency.items(),key=operator.itemgetter(1),reverse=True)[:3]       
        tags_metadata.append(tag_sentiment)
        
    return tags_metadata

In [542]:
today = str(datetime.today())
today[5:7]

'05'

In [545]:
today[6:7]

'5'

In [544]:
today

'2020-05-26 10:32:04.780812'